In [31]:
library(GO.db)
library(glue)
library(tidyverse)
library(tidytext)
library(quanteda.textstats)
library(quanteda)

if (str_detect(getwd(), "Bio_SDD")) {
    wd <- "/home/shannc/Bio_SDD/MUIC_senior_project/workflow"
    env <- "/home/shannc/Bio_SDD/miniconda3/envs/reticulate"
} else {
    wd <- "/home/shannc/workflow"
    env <- "/home/shannc/anaconda3/envs/reticulate"
}

go_file <- glue("{wd}/data/reference/go_data.tsv")
if (file.exists(go_file)) {
    info_tb <- read_tsv(go_file)
} else {
    all_gos <- as.list(GOTERM) %>% names()
    info_tb <- goInfoTb(all_gos)
    write_tsv(info_tb, go_file)
}

showFrequent <- function(tb, core_word = NULL, filter_unwanted = TRUE) {
    if (!is.null(core_word)) {
        tb <- tb %>%
            filter(grepl(core_word, term))
    }
    tb <- tb %>%
        unnest_tokens(word, term) %>%
        count(word, sort = TRUE)
    if (filter_unwanted) {
        tb %>% filter(!word %in% UNWANTED)
    } else {
        tb
    }
}


Rows: 42443 Columns: 4
── Column specification ────────────────────────────────────────────────────────
Delimiter: "\t"
chr (4): GO_IDs, term, definition, ontology

ℹ Use `spec()` to retrieve the full column specification for this data.
ℹ Specify the column types or set `show_col_types = FALSE` to quiet this message.


In [2]:
UNWANTED <- c(
    "of", "to", "cell", "in", "complex", "activity", "regulation", "process", "cellular", "stimulus",
    "response"
)

qualifiers <- c("positive", "negative", "catabolic", "involved")

In [3]:
info_tb

GO_IDs    
1     GO:0000001
2     GO:0000002
3     GO:0000003
4     GO:0000006
5     GO:0000007
6     GO:0000009
7     GO:0000010
8     GO:0000011
9     GO:0000012
10    GO:0000014
11    GO:0000015
12    GO:0000016
13    GO:0000017
14    GO:0000018
15    GO:0000019
16    GO:0000022
17    GO:0000023
18    GO:0000024
19    GO:0000025
20    GO:0000026
21    GO:0000027
22    GO:0000028
23    GO:0000030
24    GO:0000031
25    GO:0000032
26    GO:0000033
27    GO:0000034
28    GO:0000035
29    GO:0000036
30    GO:0000038
⋮     ⋮         
42414 GO:2001289
42415 GO:2001290
42416 GO:2001291
42417 GO:2001292
42418 GO:2001293
42419 GO:2001294
42420 GO:2001295
42421 GO:2001296
42422 GO:2001297
42423 GO:2001298
42424 GO:2001299
42425 GO:2001300
42426 GO:2001301
42427 GO:2001302
42428 GO:2001303
42429 GO:2001304
42430 GO:2001305
42431 GO:2001306
42432 GO:2001307
42433 GO:2001308
42434 GO:2001309
42435 GO:2001310
42436 GO:2001311
42437 GO:2001312
42438 GO:2001313
42439 GO:2001314
42440 GO:2001315
42441 GO:2001316
42442 GO:2001317
42443 all       
      term                                                               
1     mitochondrion inheritance                                          
2     mitochondrial genome maintenance                                   
3     reproduction                                                       
4     high-affinity zinc transmembrane transporter activity              
5     low-affinity zinc ion transmembrane transporter activity           
6     alpha-1,6-mannosyltransferase activity                             
7     trans-hexaprenyltranstransferase activity                          
8     vacuole inheritance                                                
9     single strand break repair                                         
10    single-stranded DNA endodeoxyribonuclease activity                 
11    phosphopyruvate hydratase complex                                  
12    lactase activity                                                   
13    alpha-glucoside transport                                          
14    regulation of DNA recombination                                    
15    regulation of mitotic recombination                                
16    mitotic spindle elongation                                         
17    maltose metabolic process                                          
18    maltose biosynthetic process                                       
19    maltose catabolic process                                          
20    alpha-1,2-mannosyltransferase activity                             
21    ribosomal large subunit assembly                                   
22    ribosomal small subunit assembly                                   
23    mannosyltransferase activity                                       
24    mannosylphosphate transferase activity                             
25    cell wall mannoprotein biosynthetic process                        
26    alpha-1,3-mannosyltransferase activity                             
27    adenine deaminase activity                                         
28    acyl binding                                                       
29    acyl carrier activity                                              
30    very long-chain fatty acid metabolic process                       
⋮     ⋮                                                                  
42414 lipid X metabolic process                                          
42415 hydroperoxide metabolic process                                    
42416 codeine metabolic process                                          
42417 codeine catabolic process                                          
42418 malonyl-CoA metabolic process                                      
42419 malonyl-CoA catabolic process                                      
42420 malonyl-CoA biosynthetic process                                   
42421 N(omega)-methyl-L-arginine metabolic process                

# Get all GO terms

In [4]:
corpus <- corpus(info_tb, text_field = "term", docid_field = "GO_IDs")
docvars(corpus) <- info_tb %>% select(., ontology, definition)
tokens <- tokens(corpus, remove_punct = TRUE)

## View top words

In [35]:
dfm <- dfm(tokens)
topfeatures(dfm, 150)

of          activity        regulation           process 
            12348             10186              9803              5662 
             cell          positive          negative                to 
             3732              3116              3069              2675 
          complex                in      biosynthetic          response 
             2312              2093              2012              1990 
          binding         metabolic          receptor           protein 
             1808              1731              1542              1540 
        catabolic          involved       development         signaling 
             1482              1470              1434              1353 
        transport           pathway          membrane              acid 
             1251              1196              1101               971 
  differentiation     transmembrane          cellular     morphogenesis 
              911               860               793               782 
        formation          assembly                by               dna 
              721               691               678               670 
      transporter          synthase            muscle     dehydrogenase 
              664               634               626               607 
             host            factor            growth               ion 
              549               529               519               506 
     localization               rna               via            kinase 
              492               482               472               452 
    proliferation        production         secretion      organization 
              451               451               420               398 
        migration              from         reductase         apoptotic 
              388               379               378               363 
          vesicle           mitotic            plasma                 t 
              357               345               343               332 
    transcription           channel     mitochondrial              fate 
              329               328               307               307 
             type                 a                ii            ligase 
              304               299               291               290 
                3           cardiac        processing            import 
              289               288               287               285 
         stimulus        activation           nuclear        polymerase 
              277               276               268               263 
    specification           calcium              into               and 
              260               260               258               258 
             body       maintenance         hydrolase                 + 
              256               248               247               238 
          antigen              mrna            immune             cycle 
              235               234               231               229 
         synaptic           hormone                 b                 i 
              229               228               223               222 
           neuron            system        epithelial           histone 
              222               219               213               212 
          spindle                 2             viral          compound 
              211               211               208               207 
      microtubule           meiotic       replication          adhesion 
              204               198               197               197 
               on    oxidoreductase          mediated     establishment 
              196               196               195               194 
          peptide               nad            across                 5 
              192               186               185               184 
             wall            smooth              rrna       phosphatase 


## Find common phrases and patterns

In [37]:
tokens %>% kwic("multicellular", window = 10)

docname    from to pre                                            
1  GO:0007275 1    1                                                 
2  GO:0022412 7    7  cellular process involved in reproduction in   
3  GO:0022608 1    1                                                 
4  GO:0022609 1    1                                                 
5  GO:0032501 1    1                                                 
6  GO:0032504 1    1                                                 
7  GO:0033555 1    1                                                 
8  GO:0035212 5    5  cell competition in a                          
9  GO:0035264 1    1                                                 
10 GO:0040014 3    3  regulation of                                  
11 GO:0040015 4    4  negative regulation of                         
12 GO:0040018 4    4  positive regulation of                         
13 GO:0044181 5    5  filamentous growth of a                        
14 GO:0046739 5    5  transport of virus in                          
15 GO:0048609 1    1                                                 
16 GO:0048871 1    1                                                 
17 GO:0050879 1    1                                                 
18 GO:0050891 1    1                                                 
19 GO:0051239 3    3  regulation of                                  
20 GO:0051240 4    4  positive regulation of                         
21 GO:0051241 4    4  negative regulation of                         
22 GO:0060586 1    1                                                 
23 GO:0071965 1    1                                                 
24 GO:0075283 7    7  sporulation resulting in formation of a        
25 GO:0075284 8    8  asexual sporulation resulting in formation of a
26 GO:0075285 8    8  sexual sporulation resulting in formation of a 
27 GO:0140962 1    1                                                 
28 GO:2000026 3    3  regulation of                                  
   keyword       post                                  pattern      
1  multicellular organism development                  multicellular
2  multicellular organism                              multicellular
3  multicellular organism adhesion                     multicellular
4  multicellular organism adhesion to substrate        multicellular
5  multicellular organismal process                    multicellular
6  multicellular organism reproduction                 multicellular
7  multicellular organismal response to stress         multicellular
8  multicellular organism                              multicellular
9  multicellular organism growth                       multicellular
10 multicellular organism growth                       multicellular
11 multicellular organism growth                       multicellular
12 multicellular organism growth                       multicellular
13 multicellular organism                              multicellular
14 multicellular host                                  multicellular
15 multicellular organismal reproductive process       multicellular
16 multicellular organismal-level homeostasis          multicellular
17 multicellular organismal movement                   multicellular
18 multicellular organismal-level water homeostasis    multicellular
19 multicellular organismal process                    multicellular
20 multicellular organismal process                    multicellular
21 multicellular organismal process                    multicellular
22 multicellular organismal-level iron ion homeostasis multicellular
23 multicellular organismal locomotion                 multicellular
24 multicellular or syncytial spore                    multicellular
25 multicellular or syncytial spore                    multicellular
26 multicellular or syncytial spore                    multicellular
27 multicellular organismal-level chemical homeostasis multicellular
28 multicellular organismal development  

In [38]:
tokens %>%
    kwic("multicellular", window = 10) %>%
    purrr::pluck("post") %>%
    unique() %>%
    discard(., \(x) str_detect(x, "involved")) %>%
    write_lines("words")

In [7]:
tokens %>%
    kwic("binding") %>%
    pluck("pre") %>%
    unique() %>%
    discard(., \(x) str_detect(x, ".*of.*|.*by.*|.*via.*")) %>%
    discard(\(x) length(str_split_1(x, " ")) > 3) %>%
    write_lines("words")


In [8]:
tokens %>% kwic("pathway") %>% pluck("pre") %>% unique() %>% discard(., \(x) str_detect(x, ".*of.*|.*by.*|.*via.*")) %>% write_lines("words")

In [9]:
tokens %>% kwic("response") %>% pluck("pre") %>% unique() %>% discard(., \(x) str_detect(x, ".*of.*|.*by.*|.*via.*")) %>% write_lines("words")

In [10]:
tokens %>% kwic("system") %>% pluck("pre") %>% discard(., \(x) str_detect(x, ".*of.*|.*by.*")) %>% unique() %>%  write_lines("systems")

In [11]:
# tokens %>% kwic("process") %>% pluck("pre") %>% unique() %>%
#     discard(., \(x) str_detect(x, ".*catabolic.*|.*biosynthetic.*|.*of.*")) %>% write_lines("processes")
read_lines("processes") %>% unique() %>% write_lines("processes")

ERROR: Error in h(simpleError(msg, call)): error in evaluating the argument 'x' in selecting a method for function 'unique': 'processes' does not exist in current working directory ('/home/shannc/Bio_SDD/MUIC_senior_project/workflow/docs').


In [ ]:
tokens %>%
    kwic("cell") %>%
    pluck("post") %>%
    unique() %>%
    discard(\(x) str_detect(x, "to$|of$|.*across.*|.*in.*|.*to.*|.*of.*|.*by.*|.*with.*|.*via.*"))

read_lines("~/cell_post") %>%
    unique() %>%
    write_lines("cell_post")


[1] "cycle"                                   
  [2] "cycle after pheromone arrest"            
  [3] "morphogenesis"                           
  [4] "plate formation"                         
  [5] "plate assembly"                          
  [6] "septum"                                  
  [7] "motility"                                
  [8] "differentiation"                         
  [9] "growth"                                  
 [10] "migration"                               
 [11] "nucleus"                                 
 [12] "fate specification"                      
 [13] "fate commitment"                         
 [14] "polarity"                                
 [15] "activation"                              
 [16] "homeostatic proliferation"               
 [17] "homeostasis"                             
 [18] "proliferation"                           
 [19] "mass cell differentiation"               
 [20] "mass cell fate commitment"               
 [21] "mass cellular morphogenesis"             
 [22] "mass cell proliferation"                 
 [23] "development"                             
 [24] "maturation"                              
 [25] "mediated immunity"                       
 [26] ""                                        
 [27] "allelic exclusion"                       
 [28] "selection"                               
 [29] "anergy"                                  
 [30] "deletion"                                
 [31] "positive selection"                      
 [32] "negative selection"                      
 [33] "chemotaxis"                              
 [34] "target"                                  
 [35] "apical basal polarity"                   
 [36] "transition"                              
 [37] "wall"                                    
 [38] "cortex"                                  
 [39] "cycle DNA replication"                   
 [40] "volume homeostasis"                      
 [41] "migration cell extension"                
 [42] "extension"                               
 [43] "migration cell contraction"              
 [44] "contraction"                             
 [45] "cycle arrest"                            
 [46] "bud growth"                              
 [47] "apical bud growth"                       
 [48] "isotropic bud growth"                    
 [49] "communication"                           
 [50] "adhesion"                                
 [51] "adhesion molecules"                      
 [52] "formation"                               
 [53] "division"                                
 [54] "migration open tracheal system"          
 [55] "recognition"                             
 [56] "death"                                   
 [57] "population proliferation"                
 [58] "shape"                                   
 [59] "size"                                    
 [60] "wall biogenesis"                         
 [61] "outer membrane"                          
 [62] "plate"                                   
 [63] "wall organization"                       
 [64] "cycle embryonic"                         
 [65] "wall modification"                       
 [66] "surface"                                 
 [67] "tip growth"                              
 [68] "wall polysaccharide metabolic process"   
 [69] "wall proteoglycan metabolic process"     
 [70] "cycle process"                           
 [71] "wall macromolecule metabolic process"    
 [72] "commitment"                              
 [73] "asymmetric division"                     
 [74] "wall macromolecule catabolic process"    
 [75] "plasma membrane"                         
 [76] "surface knob"                            
 [77] "layer development"                       
 [78] "layer maturation"                        
 [79] "layer morphogenesis"                     
 [80] "layer structural organization"           
 [81] "layer formation"                         
 [82] "precursor proliferation"  

In [ ]:
tokens %>% kwic("membrane") %>% pluck("pre") %>% unique() %>%
    discard(\(x) str_detect(x, "to$|of$|.*across.*|.*in.*|.*to.*|.*of.*|.*by.*|.*with.*|.*via.*")) %>% unique() %>% write_lines(file = "../bin/R/.membrane_nouns")

### Get collocations

In [ ]:
collocations <- tokens %>% textstat_collocations() %>% as_tibble()

In [ ]:
collocations <- collocations %>% arrange(desc(count))
a <- collocations %>% filter(!grepl("process|activity|regulation", collocation))
b <- collocations %>% filter(grepl("receptor", collocation))

In [ ]:
corpus %>%
  corpus_subset(., grepl("process,", as.character(corpus))) %>%
  tokens(remove_punct = TRUE) %>%
  textstat_collocations()

collocation                         count count_nested length lambda   
1  regulation of                       14    0            2       8.251612
2  nuclear-transcribed mrna            21    0            2      10.239710
3  isopentenyl diphosphate              9    0            2       8.357572
4  mrna catabolic                      21    0            2       7.267232
5  propionate metabolic                 2    0            2       5.941632
6  of nuclear-transcribed               9    0            2       6.730143
7  3 5                                  2    0            2       5.427883
8  5 3                                  2    0            2       5.427883
9  biosynthetic process                31    0            2       6.275268
10 sulfate proteoglycan                 5    0            2       8.924390
11 negative regulation                  5    0            2       6.715383
12 catabolic process                   30    0            2       6.213593
13 mevalonate pathway                   6    0            2       6.505784
14 exonucleolytic nonsense-mediated     2    0            2       4.320447
15 meiosis-specific transcripts         4    0            2       8.726643
16 methylerythritol 4-phosphate         4    0            2       8.726643
17 nonsense-mediated decay              6    0            2       6.359689
18 heparan sulfate                      3    0            2       6.862967
19 myo-inositol hexakisphosphate        3    0            2       8.478244
20 polysaccharide chain                 3    0            2       8.478244
21 positive regulation                  4    0            2       6.314042
22 diphosphate biosynthetic            10    0            2       5.730628
23 by transamination                    2    0            2       6.529419
24 in terpenoid                         2    0            2       8.144679
25 involved in                          2    0            2       8.144679
26 pathway involved                     2    0            2       8.144679
27 4-phosphate pathway                  4    0            2       5.869795
28 of isopentenyl                       5    0            2       5.756155
29 deadenylation-dependent decay        4    0            2       5.755576
30 proteoglycan biosynthetic            5    0            2       4.874909
31 terpenoid biosynthetic               4    0            2       4.637197
32 process mevalonate                   6    0            2       4.246491
33 chain biosynthetic                   3    0            2       4.350165
34 hexakisphosphate biosynthetic        3    0            2       4.350165
35 process nonsense-mediated            4    0            2       2.225646
36 catechol catabolic                   2    0            2       4.016857
37 protocatechuate catabolic            2    0            2       4.016857
38 process by                           4    0            2       3.842064
39 process deadenylation-dependent      4    0            2       3.842064
40 process meiosis-specific             4    0            2       3.842064
41 process methylerythritol             4    0            2       3.842064
42 peptidyl-1-thioglycine biosynthetic  2    0            2       3.979206
43 process polysaccharide               3    0            2       3.572892
44 process exonucleolytic               3    0            2       1.956474
45 metabolic process                    3    0            2       3.470552
46 process meta-cleavage                2    0            2       3.218876
47 process ortho-cleavage               2    0            2       3.218876
48 process using                        2    0            2       3.218876
   z       
1  5.248260
2  5.088414
3  5.017141
4  4.950533
5  4.509197
6  4.495138
7  4.477459
8  4.477459
9  4.366745
10 4.362586
11 4.328451
12 4.323644
13 4.279860
14 4.267066
15 4.245478
16 4.245478
17 4.202438
18 4.185481
19 4.093991
20 4.093991
21 4.069763
22 3.912882
23 3.900041
24 3.881543
25 3.881543
26 3.881543
27 3

### Searches on specific terms

In [ ]:
process <- tokens %>% kwic("process")
process$pre %>% unique()

[1] "maltose metabolic"                                                                    
   [2] "maltose biosynthetic"                                                                 
   [3] "maltose catabolic"                                                                    
   [4] "cell wall mannoprotein biosynthetic"                                                  
   [5] "very long-chain fatty acid metabolic"                                                 
   [6] "citrulline metabolic"                                                                 
   [7] "argininosuccinate metabolic"                                                          
   [8] "sulfur amino acid metabolic"                                                          
   [9] "sulfur amino acid biosynthetic"                                                       
  [10] "sulfur amino acid catabolic"                                                          
  [11] "histidine biosynthetic"                                                               
  [12] "tryptophan biosynthetic"                                                              
  [13] "nuclear-transcribed mRNA catabolic"                                                   
  [14] "allantoin metabolic"                                                                  
  [15] "allantoin catabolic"                                                                  
  [16] "peptidoglycan metabolic"                                                              
  [17] "polysaccharide biosynthetic"                                                          
  [18] "polysaccharide catabolic"                                                             
  [19] "RNA fragment catabolic"                                                               
  [20] "glutamine family amino acid metabolic"                                                
  [21] "regulation of arginine metabolic"                                                     
  [22] "amino acid catabolic"                                                                 
  [23] "aromatic amino acid family catabolic"                                                 
  [24] "branched-chain amino acid catabolic"                                                  
  [25] "methionine catabolic"                                                                 
  [26] "mitochondrial RNA catabolic"                                                          
  [27] "mitochondrial mRNA catabolic"                                                         
  [28] "mitochondrial RNA metabolic"                                                          
  [29] "regulation of mitochondrial RNA catabolic"                                            
  [30] "acetylcholine catabolic"                                                              
  [31] "prostaglandin biosynthetic"                                                           
  [32] "retinoid metabolic"                                                                   
  [33] "lactosylceramide biosynthetic"                                                        
  [34] "ganglioside metabolic"                                                                
  [35] "ganglioside biosynthetic"                                                             
  [36] "globoside metabolic"                                                                  
  [37] "globoside biosynthetic"                                                               
  [38] "long-chain fatty acid metabolic"                                                      
  [39] "histamine metabolic"                                                                  
  [40] "histamine biosynthetic"                                                               
  [41] "histamine catabolic"                                                                  
  [42] "neutrophil apoptotic"                                                                 
  [43] "B cel

In [ ]:
activity <- tokens %>% kwic("activity")

In [ ]:
pathways <- tokens %>% kwic("pathway")
pathways

docname    from to pre                                                    
1    GO:0000754  4    4 adaptation of signaling                                
2    GO:0000766  5    5 negative adaptation of signaling                       
3    GO:0000947  9    9 process to alcohol via Ehrlich                         
4    GO:0000948 10   10 to carboxylic acid via Ehrlich                         
5    GO:0000949 11   11 process to alcohol via Ehrlich                         
6    GO:0000950 10   10 process to alcohol via Ehrlich                         
7    GO:0000952 12   12 to carboxylic acid via Ehrlich                         
8    GO:0000953 11   11 to carboxylic acid via Ehrlich                         
9    GO:0000955  7    7 acid catabolic process via Ehrlich                     
10   GO:0001867  4    4 complement activation lectin                           
11   GO:0001868  6    6 regulation of complement activation lectin             
12   GO:0001869  7    7 regulation of complement activation lectin             
13   GO:0001870  7    7 regulation of complement activation lectin             
14   GO:0001959  5    5 regulation of cytokine-mediated signaling              
15   GO:0001960  6    6 negative regulation of cytokine-mediated signaling     
16   GO:0001961  6    6 positive regulation of cytokine-mediated signaling     
17   GO:0001973  6    6 G protein-coupled adenosine receptor signaling         
18   GO:0002029  7    7 of G protein-coupled receptor signaling                
19   GO:0002032  7    7 of G protein-coupled receptor signaling                
20   GO:0002154  5    5 thyroid hormone mediated signaling                     
21   GO:0002155  7    7 of thyroid hormone mediated signaling                  
22   GO:0002156  8    8 of thyroid hormone mediated signaling                  
23   GO:0002157  8    8 of thyroid hormone mediated signaling                  
24   GO:0002220  9    9 activating cell surface receptor signaling             
25   GO:0002221  5    5 pattern recognition receptor signaling                 
26   GO:0002222  7    7 killer cell immunoglobulin-like receptor signaling     
27   GO:0002223  6    6 stimulatory C-type lectin receptor signaling           
28   GO:0002224  4    4 toll-like receptor signaling                           
29   GO:0002429  7    7 response-activating cell surface receptor signaling    
30   GO:0002430  5    5 complement receptor mediated signaling                 
⋮    ⋮          ⋮    ⋮  ⋮                                                      
1167 GO:2000734 10   10 cell-derived neurotrophic factor receptor signaling    
1168 GO:2000735 10   10 cell-derived neurotrophic factor receptor signaling    
1169 GO:2000764  6    6 positive regulation of semaphorin-plexin signaling     
1170 GO:2000796  3    3 Notch signaling                                        
1171 GO:2001044  5    5 regulation of integrin-mediated signaling              
1172 GO:2001045  6    6 negative regulation of integrin-mediated signaling     
1173 GO:2001046  6    6 positive regulation of integrin-mediated signaling     
1174 GO:2001159  8    8 protein localization by the Cvt                        
1175 GO:2001210  8    8 isopentenyl diphosphate biosynthetic process mevalonate
1176 GO:2001211  9    9 isopentenyl diphosphate biosynthetic process mevalonate
1177 GO:2001233  5    5 regulation of apoptotic signaling                      
1178 GO:2001234  6    6 negative regulation of apoptotic signaling             
1179 GO:2001235  6    6 positive regulation of apoptotic signaling             
1180 GO:2001236  6    6 regulation of extrinsic apoptotic signaling            
1181 GO:2001237  7    7 regulation of extrinsic apoptotic signaling            
1182 GO:2001238  7    7 regulation of extrinsic apoptotic signaling            
1183 GO:2001239  6    6 regulation of extrinsic apoptotic signaling            
1184 GO:2001240  7    7 regulation of extrinsic apoptotic signaling            
1185 

In [ ]:
tokens %>% kwic("cell")

docname    from to pre                                     keyword
1    GO:0000032 1    1                                          cell   
2    GO:0000075 1    1                                          cell   
3    GO:0000082 6    6  G1 S transition of mitotic              cell   
4    GO:0000086 6    6  G2 M transition of mitotic              cell   
5    GO:0000196 1    1                                          cell   
6    GO:0000278 2    2  mitotic                                 cell   
7    GO:0000320 4    4  re-entry into mitotic                   cell   
8    GO:0000321 4    4  re-entry into mitotic                   cell   
9    GO:0000751 2    2  mitotic                                 cell   
10   GO:0000753 1    1                                          cell   
11   GO:0000902 1    1                                          cell   
12   GO:0000911 3    3  cytokinesis by                          cell   
13   GO:0000919 1    1                                          cell   
14   GO:0000934 2    2  porous                                  cell   
15   GO:0000936 2    2  primary                                 cell   
16   GO:0001539 4    4  cilium or flagellum-dependent           cell   
17   GO:0001549 2    2  cumulus                                 cell   
18   GO:0001558 3    3  regulation of                           cell   
19   GO:0001560 3    3  regulation of                           cell   
20   GO:0001667 2    2  ameboidal-type                          cell   
21   GO:0001673 3    3  male germ                               cell   
22   GO:0001674 3    3  female germ                             cell   
23   GO:0001708 1    1                                          cell   
24   GO:0001709 1    1                                          cell   
25   GO:0001710 2    2  mesodermal                              cell   
26   GO:0001711 2    2  endodermal                              cell   
27   GO:0001712 2    2  ectodermal                              cell   
28   GO:0001713 2    2  ectodermal                              cell   
29   GO:0001714 2    2  endodermal                              cell   
30   GO:0001715 2    2  ectodermal                              cell   
⋮    ⋮          ⋮    ⋮  ⋮                                       ⋮      
3703 GO:2001053  4    4 regulation of mesenchymal               cell   
3704 GO:2001054  5    5 negative regulation of mesenchymal      cell   
3705 GO:2001055  5    5 positive regulation of mesenchymal      cell   
3706 GO:2001109  5    5 regulation of lens epithelial           cell   
3707 GO:2001110  6    6 negative regulation of lens epithelial  cell   
3708 GO:2001111  6    6 positive regulation of lens epithelial  cell   
3709 GO:2001185  6    6 regulation of CD8-positive alpha-beta T cell   
3710 GO:2001186  7    7 regulation of CD8-positive alpha-beta T cell   
3711 GO:2001187  7    7 regulation of CD8-positive alpha-beta T cell   
3712 GO:2001188  4    4 regulation of T                         cell   
3713 GO:2001188  8    8 T cell activation via T                 cell   
3714 GO:2001188 20   20 MHC molecule on antigen presenting      cell   
3715 GO:2001189  5    5 negative regulation of T                cell   
3716 GO:2001189  9    9 T cell activation via T                 cell   
3717 GO:2001189 21   21 MHC molecule on antigen presenting      cell   
3718 GO:2001190  5    5 positive regulation of T                cell   
3719 GO:2001190  9    9 T cell activation via T                 cell   
3720 GO:2001190 21   21 MHC molecule on antigen presenting      cell   
3721 GO:2001191  5    5 regulation of gamma-delta T             cell   
3722 GO:2001192  6    6 negative regulation of gamma-delta T    cell   
3723 GO:2001193  6    6 positive regulation of gamma-delta T    cell   
3724 GO:2001198  4    4 regulation of dendritic                 cell   
3725 GO:2001199  5    5 negative regulation of dendritic        cell   
3726 GO:2001200  5    5 positive regulation o

### Test compounding

In [ ]:
tokens_compound(tokens, pattern = "of * activity", valuetype = "regex") %>% kwic("activity")

docname    from to
1     GO:0000006 5    5 
2     GO:0000007 6    6 
3     GO:0000009 2    2 
4     GO:0000010 2    2 
5     GO:0000014 4    4 
6     GO:0000016 2    2 
7     GO:0000026 2    2 
8     GO:0000030 2    2 
9     GO:0000031 3    3 
10    GO:0000033 2    2 
11    GO:0000034 3    3 
12    GO:0000036 3    3 
13    GO:0000048 2    2 
14    GO:0000064 4    4 
15    GO:0000079 8    8 
16    GO:0000095 4    4 
17    GO:0000099 6    6 
18    GO:0000100 4    4 
19    GO:0000102 6    6 
20    GO:0000104 3    3 
21    GO:0000107 3    3 
22    GO:0000121 2    2 
23    GO:0000140 3    3 
24    GO:0000146 3    3 
25    GO:0000150 4    4 
26    GO:0000155 4    4 
27    GO:0000156 4    4 
28    GO:0000170 3    3 
29    GO:0000171 3    3 
30    GO:0000175 5    5 
⋮     ⋮          ⋮    ⋮ 
10157 GO:2000468 4    4 
10158 GO:2000469 5    5 
10159 GO:2000470 5    5 
10160 GO:2000479 6    6 
10161 GO:2000480 7    7 
10162 GO:2000481 7    7 
10163 GO:2000649 7    7 
10164 GO:2000650 8    8 
10165 GO:2000651 8    8 
10166 GO:2000825 6    6 
10167 GO:2000969 6    6 
10168 GO:2000983 6    6 
10169 GO:2000984 7    7 
10170 GO:2000985 7    7 
10171 GO:2001056 6    6 
10172 GO:2001106 7    7 
10173 GO:2001107 8    8 
10174 GO:2001108 8    8 
10175 GO:2001144 5    5 
10176 GO:2001145 6    6 
10177 GO:2001146 6    6 
10178 GO:2001257 5    5 
10179 GO:2001258 6    6 
10180 GO:2001259 6    6 
10181 GO:2001267 5    5 
10182 GO:2001268 6    6 
10183 GO:2001269 6    6 
10184 GO:2001270 5    5 
10185 GO:2001271 6    6 
10186 GO:2001272 6    6 
      pre                                                                          
1     high-affinity zinc transmembrane transporter                                 
2     low-affinity zinc ion transmembrane transporter                              
3     alpha-1,6-mannosyltransferase                                                
4     trans-hexaprenyltranstransferase                                             
5     single-stranded DNA endodeoxyribonuclease                                    
6     lactase                                                                      
7     alpha-1,2-mannosyltransferase                                                
8     mannosyltransferase                                                          
9     mannosylphosphate transferase                                                
10    alpha-1,3-mannosyltransferase                                                
11    adenine deaminase                                                            
12    acyl carrier                                                                 
13    peptidyltransferase                                                          
14    L-ornithine transmembrane transporter                                        
15    cyclin-dependent protein serine threonine kinase                             
16    S-adenosyl-L-methionine transmembrane transporter                            
17    sulfur amino acid transmembrane transporter                                  
18    S-methylmethionine transmembrane transporter                                 
19    L-methionine secondary active transmembrane transporter                      
20    succinate dehydrogenase                                                      
21    imidazoleglycerol-phosphate synthase                                         
22    glycerol-1-phosphatase                                                       
23    acylglycerone-phosphate reductase                                            
24    microfilament motor                                                          
25    DNA strand exchange                                                          
26    phosphorelay sensor kinase                                                   
27    phosphorelay response regulator                                              
28    sphingosine hydroxylase                                                      
29    ribonuclease M

quanteda is good for defined phrases, but it looks like you'll have to rely on stringr for advanced regex first

### Terms with "activity"

In [ ]:
activity <- info_tb %>% filter(grepl("activity", term))
samples <- activity$term

compoundActivity <- function(str) {
  match <- str_match(str, "^(?:.*of)?(.*)activity(?:.*in)?(.*)?")
  first <- match[, 2] %>%
    str_trim() %>%
    str_replace_all(., " ", "_")
  sec <- match[, 3] %>%
    str_trim() %>%
    str_replace_all(., " ", "_")
  return(str_trim(paste0(first, " ", sec)))
}

compoundActivity(samples) %>% tail()

[1] "cysteine-type_endopeptidase g_pathway"                   
[2] "cysteine-type_endopeptidase g_pathway"                   
[3] "cysteine-type_endopeptidase g_pathway"                   
[4] "cysteine-type_endopeptidase execution_phase_of_apoptosis"
[5] "cysteine-type_endopeptidase execution_phase_of_apoptosis"
[6] "cysteine-type_endopeptidase execution_phase_of_apoptosis"

In [ ]:
activity$term

[1] "high-affinity zinc transmembrane transporter activity"                                                                                                                                      
    [2] "low-affinity zinc ion transmembrane transporter activity"                                                                                                                                   
    [3] "alpha-1,6-mannosyltransferase activity"                                                                                                                                                     
    [4] "trans-hexaprenyltranstransferase activity"                                                                                                                                                  
    [5] "single-stranded DNA endodeoxyribonuclease activity"                                                                                                                                         
    [6] "lactase activity"                                                                                                                                                                           
    [7] "alpha-1,2-mannosyltransferase activity"                                                                                                                                                     
    [8] "mannosyltransferase activity"                                                                                                                                                               
    [9] "mannosylphosphate transferase activity"                                                                                                                                                     
   [10] "alpha-1,3-mannosyltransferase activity"                                                                                                                                                     
   [11] "adenine deaminase activity"                                                                                                                                                                 
   [12] "acyl carrier activity"                                                                                                                                                                      
   [13] "peptidyltransferase activity"                                                                                                                                                               
   [14] "L-ornithine transmembrane transporter activity"                                                                                                                                             
   [15] "regulation of cyclin-dependent protein serine/threonine kinase activity"                                                                                                                    
   [16] "S-adenosyl-L-methionine transmembrane transporter activity"                                                                                                                                 
   [17] "sulfur amino acid transmembrane transporter activity"                                                                                                                                       
   [18] "S-methylmethionine transmembrane transporter activity"                                                                                                                                      
   [19] "L-methionine secondary active transmembrane transporter activity"                                                                                                                           
   [20] "succinate dehydrogenase activity"                                                                                                                                                           
   [21] "imidazoleglycerol-phosphate synthas

In [ ]:
# General version of above
compoundSpecial <- function(str, pattern, expected_matches) {
  match <- str_match(str, pattern)
  selected <- lapply(seq(2, expected_matches + 1), \(x)  {
    match[, x] %>%
      str_trim() %>%
      str_replace_all(., " ", "_")
  })
  reduce(selected, \(x, y) paste0(x, " ", y)) %>% str_trim()
}

compoundSpecial(samples, "^(?:.*of)?(.*)activity(?:.*in)?(.*)?", 2) %>% tail()

[1] "cysteine-type_endopeptidase g_pathway"                   
[2] "cysteine-type_endopeptidase g_pathway"                   
[3] "cysteine-type_endopeptidase g_pathway"                   
[4] "cysteine-type_endopeptidase execution_phase_of_apoptosis"
[5] "cysteine-type_endopeptidase execution_phase_of_apoptosis"
[6] "cysteine-type_endopeptidase execution_phase_of_apoptosis"

### Terms with "regulation"

In [ ]:
regulation <- info_tb %>% filter(ontology == "BP") %>% filter(grepl("regulation", term))
regulation$term %>% keep(\(x) grepl("activity", x)) %>%
    compoundSpecial("^(?:.*of)?(.*)activity(?:.*in)?(.*)?", 2)

# compoundSpecial(regulation$term, "^(?:.*of)?(.*)(?:.*from)?(.*)", 2)

[1] "cyclin-dependent_protein_serine/threonine_kinase"                                               
  [2] "protein_kinase"                                                                                 
  [3] "epidermal_growth_factor-activated_receptor"                                                     
  [4] "epidermal_growth_factor-activated_receptor"                                                     
  [5] "adenylate_cyclase"                                                                              
  [6] "anion_channel"                                                                                  
  [7] "anion_channel"                                                                                  
  [8] "anion_channel by_blue_light"                                                                    
  [9] "anion_channel by_blue_light"                                                                    
 [10] "light-activated_voltage-gated_calcium_channel"                                                  
 [11] "peptidase"                                                                                      
 [12] "signaling_receptor"                                                                             
 [13] "phospholipase"                                                                                  
 [14] "phospholipase"                                                                                  
 [15] "phospholipase"                                                                                  
 [16] "Janus_kinase"                                                                                   
 [17] "Janus_kinase"                                                                                   
 [18] "adenylate_cyclase g_pathway"                                                                    
 [19] "alkaline_phosphatase"                                                                           
 [20] "alkaline_phosphatase"                                                                           
 [21] "alkaline_phosphatase"                                                                           
 [22] "ferrochelatase"                                                                                 
 [23] "proton-transporting_ATPase ,_rotational_mechanism"                                              
 [24] "phospholipase_C"                                                                                
 [25] "protein_histidine_kinase"                                                                       
 [26] "epimerase"                                                                                      
 [27] "isomerase"                                                                                      
 [28] "isomerase"                                                                                      
 [29] "phosphatase"                                                                                    
 [30] "phosphatase"                                                                                    
 [31] "phosphatase"                                                                                    
 [32] "inositol-polyphosphate_5-phosphatase"                                                           
 [33] "inositol-polyphosphate_5-phosphatase"                                                           
 [34] "endopeptidase"                                                                                  
 [35] "endopeptidase"                                                                                  
 [36] "peptidase"                                                                                      
 [37] "calcidiol_1-monooxygenase"                                                                      
 [38] "vitamin_D_24-hydroxylase"                                                                       
 [39] "vitamin_D_24-hydroxylase"                  

### Terms with "pathway"

In [ ]:
pathways <- info_tb %>% filter(grepl("pathway", term))
pathways$term

[1] "adaptation of signaling pathway by response to pheromone involved in conjugation with cellular fusion"                                                    
   [2] "negative adaptation of signaling pathway by response to pheromone involved in pheromone-induced unidirectional conjugation"                               
   [3] "amino acid catabolic process to alcohol via Ehrlich pathway"                                                                                              
   [4] "amino acid catabolic process to carboxylic acid via Ehrlich pathway"                                                                                      
   [5] "aromatic amino acid family catabolic process to alcohol via Ehrlich pathway"                                                                              
   [6] "branched-chain amino acid catabolic process to alcohol via Ehrlich pathway"                                                                               
   [7] "aromatic amino acid family catabolic process to carboxylic acid via Ehrlich pathway"                                                                      
   [8] "branched-chain amino acid catabolic process to carboxylic acid via Ehrlich pathway"                                                                       
   [9] "amino acid catabolic process via Ehrlich pathway"                                                                                                         
  [10] "complement activation, lectin pathway"                                                                                                                    
  [11] "regulation of complement activation, lectin pathway"                                                                                                      
  [12] "negative regulation of complement activation, lectin pathway"                                                                                             
  [13] "positive regulation of complement activation, lectin pathway"                                                                                             
  [14] "regulation of cytokine-mediated signaling pathway"                                                                                                        
  [15] "negative regulation of cytokine-mediated signaling pathway"                                                                                               
  [16] "positive regulation of cytokine-mediated signaling pathway"                                                                                               
  [17] "G protein-coupled adenosine receptor signaling pathway"                                                                                                   
  [18] "desensitization of G protein-coupled receptor signaling pathway"                                                                                          
  [19] "desensitization of G protein-coupled receptor signaling pathway by arrestin"                                                                              
  [20] "thyroid hormone mediated signaling pathway"                                                                                                               
  [21] "regulation of thyroid hormone mediated signaling pathway"                                                                                                 
  [22] "negative regulation of thyroid hormone mediated signaling pathway"                                                                                        
  [23] "positive regulation of thyroid hormone mediated signaling pathway"                                                                                        
  [24] "innate immune response activating cell surface receptor signaling pathway"                                                                                
  [25] "pattern recognition receptor signaling pathway"                                    

In [ ]:
# bind pathways into single tokens, replacing this in the original name
f <- function(x) {
    str_replace(x, " ", "_")
}

pnames <- pathways$term %>% compoundSpecial("(?:.* in)?(?:.*of)?(?:.*via)?(.*pathway)", 1)
context1 <- pathways$term %>% str_extract(".*( in| via| of)") %>% map_chr(., \(x) ifelse(is.na(x), "", x))
context2 <- pathways$term %>% str_extract("pathway (.*)", group = 1) %>% map_chr(., \(x) ifelse(is.na(x), "", x))
paste0(context1, " ", pnames, " ", context2)

[1] "adaptation of signaling pathway by response to pheromone involved in signaling_pathway by response to pheromone involved in conjugation with cellular fusion"                                                                                                                     
   [2] "negative adaptation of signaling pathway by response to pheromone involved in signaling_pathway by response to pheromone involved in pheromone-induced unidirectional conjugation"                                                                                                
   [3] "amino acid catabolic process to alcohol via Ehrlich_pathway "                                                                                                                                                                                                                     
   [4] "amino acid catabolic process to carboxylic acid via Ehrlich_pathway "                                                                                                                                                                                                             
   [5] "aromatic amino acid family catabolic process to alcohol via Ehrlich_pathway "                                                                                                                                                                                                     
   [6] "branched-chain amino acid catabolic process to alcohol via Ehrlich_pathway "                                                                                                                                                                                                      
   [7] "aromatic amino acid family catabolic process to carboxylic acid via Ehrlich_pathway "                                                                                                                                                                                             
   [8] "branched-chain amino acid catabolic process to carboxylic acid via Ehrlich_pathway "                                                                                                                                                                                              
   [9] "amino acid catabolic process via Ehrlich_pathway "                                                                                                                                                                                                                                
  [10] " complement_activation,_lectin_pathway "                                                                                                                                                                                                                                          
  [11] "regulation of complement_activation,_lectin_pathway "                                                                                                                                                                                                                             
  [12] "negative regulation of complement_activation,_lectin_pathway "                                                                                                                                                                                                                    
  [13] "positive regulation of complement_activation,_lectin_pathway "                                                                                                                                                                                                                    
  [14] "regulation of cytokine-mediated_signaling_pathway "                                                                                                                                                                                                                               
  [15] "negative regulation of cytokine-m

### Terms with "process"

In [ ]:
process <- info_tb %>% filter(grepl("process", term) & grepl("biosynthetic|metabolic|catabolic", term)) %>%
  mutate(type = map_chr(term, \(x) {
    case_when(
      str_detect(x, "catabolic") ~ "catabolic",
      str_detect(x, "biosynthetic") ~ "anabolic",
      .default = "unspecified"
    )
  }))

In [ ]:
process$term %>% corpus() %>% tokens() %>% textstat_collocations() %>% as_tibble() %>% arrange(desc(count))

collocation                   count count_nested length lambda     
1    biosynthetic process          2012  0            2       9.608525  
2    metabolic process             1729  0            2       9.372527  
3    catabolic process             1482  0            2       9.150128  
4    regulation of                 1234  0            2      12.016198  
5    positive regulation            389  0            2      10.417621  
6    negative regulation            379  0            2      10.365670  
7    process from                   124  0            2       7.744914  
8    acid biosynthetic              122  0            2       1.603711  
9    process to                     121  0            2       6.821337  
10   acid metabolic                 104  0            2       1.524768  
11   process via                     81  0            2       5.033600  
12   protein catabolic               66  0            2       3.743712  
13   acid catabolic                  65  0            2       1.039459  
14   cell wall                       60  0            2      10.914269  
15   amino acid                      56  0            2       5.988012  
16   compound metabolic              46  0            2       1.801771  
17   fatty acid                      43  0            2       6.568671  
18   involved in                     39  0            2      11.862443  
19   mrna catabolic                  37  0            2       4.308634  
20   compound catabolic              36  0            2       1.592589  
21   compound biosynthetic           34  0            2       1.166064  
22   methane biosynthetic            33  0            2       4.637955  
23   a biosynthetic                  31  0            2       2.140042  
24   diphosphate biosynthetic        30  0            2       1.975670  
25   > 3                             28  0            2       9.518168  
26   of methane                      24  0            2       6.466138  
27   nuclear-transcribed mrna        23  0            2      10.732702  
28   process involved                21  0            2       3.986284  
29   of cellular                     20  0            2       4.675024  
30   c biosynthetic                  19  0            2       2.264295  
⋮    ⋮                             ⋮     ⋮            ⋮      ⋮          
1493 ceramide metabolic            2     0            2       0.97214990
1494 glucosinolate metabolic       2     0            2       0.97214990
1495 raffinose metabolic           2     0            2       0.97214990
1496 molecule biosynthetic         2     0            2       0.92806076
1497 ether biosynthetic            2     0            2       0.80283142
1498 fatty-acyl-coa biosynthetic   2     0            2       0.80283142
1499 starch biosynthetic           2     0            2       0.80283142
1500 of chitin                     2     0            2       0.73079728
1501 of proteoglycan               2     0            2       0.73079728
1502 glycoprotein catabolic        2     0            2       0.67800775
1503 carbohydrate biosynthetic     2     0            2       0.69153957
1504 anchor metabolic              2     0            2       0.66967399
1505 primary metabolic             2     0            2       0.66967399
1506 histidine metabolic           2     0            2       0.58622736
1507 amine biosynthetic            2     0            2       0.59138990
1508 ketone biosynthetic           2     0            2       0.59138990
1509 toluene biosynthetic          2     0            2       0.59138990
1510 of polysaccharide             2     0            2       0.55367736
1511 amide biosynthetic            2     0            2       0.50035191
1512 glycerol biosynthetic         2     0            2       0.50035191
1513 II metabolic                  2     0            2       0.37092090
1514 chlorophyll metabolic         2     0            2       0.37092090
1515 alpha-glucan catabolic        2     0            2       0

In [ ]:
process$term %>% corpus() %>% tokens() %>% kwic("fructose")

docname  from to pre                                         keyword 
1  text106  1    1                                              fructose
2  text107  1    1                                              fructose
3  text108  1    1                                              fructose
4  text109  1    1                                              fructose
5  text1346 2    2  anaerobic                                   fructose
6  text1531 2    2  aerobic                                     fructose
7  text1686 1    1                                              fructose
8  text2895 1    1                                              fructose
9  text3285 3    3  regulation of                               fructose
10 text3286 4    4  positive regulation of                      fructose
11 text3307 1    1                                              fructose
12 text3308 9    9  to fructose-6-phosphate through glucose and fructose
   post                                          pattern 
1  metabolic process                             fructose
2  catabolic process                             fructose
3  6-phosphate metabolic process                 fructose
4  2,6-bisphosphate metabolic process            fructose
5  catabolic process                             fructose
6  catabolic process                             fructose
7  1,6-bisphosphate metabolic process            fructose
8  biosynthetic process                          fructose
9  1,6-bisphosphate metabolic process            fructose
10 1,6-bisphosphate metabolic process            fructose
11 catabolic process to hydroxyacetone phosphate fructose
12                                               fructose

In [ ]:
process$term %>% compoundSpecial(., "^(?:.*of)?(.*)(?:metabolic|catabolic|biosynthetic.*)", 1)

[1] "maltose"                                                                                                 
   [2] "maltose"                                                                                                 
   [3] "maltose"                                                                                                 
   [4] "cell_wall_mannoprotein"                                                                                  
   [5] "very_long-chain_fatty_acid"                                                                              
   [6] "citrulline"                                                                                              
   [7] "argininosuccinate"                                                                                       
   [8] "sulfur_amino_acid"                                                                                       
   [9] "sulfur_amino_acid"                                                                                       
  [10] "sulfur_amino_acid"                                                                                       
  [11] "histidine"                                                                                               
  [12] "tryptophan"                                                                                              
  [13] "nuclear-transcribed_mRNA"                                                                                
  [14] "allantoin"                                                                                               
  [15] "allantoin"                                                                                               
  [16] "peptidoglycan"                                                                                           
  [17] "polysaccharide"                                                                                          
  [18] "polysaccharide"                                                                                          
  [19] "nuclear-transcribed_mRNA"                                                                                
  [20] "nuclear-transcribed_mRNA"                                                                                
  [21] "RNA_fragment"                                                                                            
  [22] "nuclear-transcribed_mRNA"                                                                                
  [23] "glutamine_family_amino_acid"                                                                             
  [24] "arginine"                                                                                                
  [25] "amino_acid"                                                                                              
  [26] "amino_acid"                                                                                              
  [27] "aromatic_amino_acid_family"                                                                              
  [28] "branched-chain_amino_acid"                                                                               
  [29] "methionine"                                                                                              
  [30] "aromatic_amino_acid_family"                                                                              
  [31] "branched-chain_amino_acid"                                                                               
  [32] "methionine"                                                                                              
  [33] "amino_acid"                                                                                              
  [34] "nuclear-transcribed_mRNA"                                                                                
  [35] "mitochondrial_RNA"                                                                                       
  [36] "mitoc

# Find verbs used in each sub-ontology

In [ ]:
cc <- corpus_subset(corpus, ontology == "CC")
cc_tokens <- cc %>% tokens(remove_punct = TRUE)
cc_tokens %>% textstat_collocations()

collocation                 count count_nested length lambda     
1    host cell                   75    0            2      5.774402   
2    collagen type               29    0            2      6.913928   
3    endoplasmic reticulum       44    0            2      8.514725   
4    transport vesicle           33    0            2      5.502378   
5    RNA polymerase              31    0            2      7.969458   
6    transcription factor        22    0            2      4.854412   
7    mitotic spindle             18    0            2      6.876903   
8    extracellular matrix        17    0            2      6.357154   
9    spindle pole                22    0            2      7.726801   
10   cytoplasmic side            18    0            2      4.953262   
11   basal body                  23    0            2      5.101172   
12   viral capsid                24    0            2      7.067780   
13   plasma membrane             52    0            2      4.898189   
14   DNA polymerase              14    0            2      4.940085   
15   vesicle lumen               19    0            2      3.933409   
16   ubiquitin ligase            46    0            2      9.267609   
17   actin filament              11    0            2      5.657919   
18   vesicle membrane            34    0            2      3.135494   
19   outer membrane              33    0            2      3.368124   
20   histone acetyltransferase   11    0            2      7.687230   
21   protein kinase              15    0            2      4.709545   
22   proteasome regulatory        9    0            2      6.347841   
23   regulatory particle          9    0            2      6.170571   
24   contractile ring            10    0            2      6.185458   
25   proton-transporting ATP     21    0            2      8.377452   
26   endocytic zone               8    0            2      6.375105   
27   flagellum basal              8    0            2      6.236728   
28   pole body                   18    0            2      5.776175   
29   proteasome core              9    0            2      5.179032   
30   icosahedral viral           16    0            2      8.301715   
⋮    ⋮                           ⋮     ⋮            ⋮      ⋮          
1053 checkpoint complex          2     0            2       1.29742159
1054 hormone complex             2     0            2       1.29742159
1055 of transport                2     0            2       0.92544445
1056 postsynaptic membrane       3     0            2       0.79584587
1057 nuclear body                2     0            2       0.90898777
1058 of outer                    2     0            2       0.90207187
1059 initiation complex          4     0            2       0.78692871
1060 repair complex              4     0            2       0.78692871
1061 II complex                  9     0            2       0.48161210
1062 clamp complex               2     0            2       0.96080602
1063 endopeptidase complex       2     0            2       0.96080602
1064 glycoprotein complex        2     0            2       0.96080602
1065 transfer complex            2     0            2       0.96080602
1066 mitochondrial membrane      5     0            2       0.50440869
1067 plastid membrane            2     0            2       0.58449560
1068 mannosyltransferase complex 2     0            2       0.50853418
1069 secretion complex           2     0            2       0.19809245
1070 b complex                   2     0            2      -0.03858321
1071 junction complex            2     0            2      -0.03858321
1072 c complex                   4     0            2      -0.06180439
1073 transport complex           9     0            2      -0.10343925
1074 myosin complex              4     0            2      -0.31383720
1075 apical complex              3     0            2      -0.42214463
1076 replication complex         2     0            2      -0.52899258
1077 proteasome complex      

In [ ]:
mf <- corpus_subset(corpus, ontology == "MF")
mf_tokens <- mf %>% tokens(remove_punct = TRUE)
mf_tokens %>% textstat_collocations() %>% as_tibble() %>% arrange(desc(count))

collocation                count count_nested length lambda     
1    transporter activity       600   0            2       4.9839297 
2    synthase activity          501   0            2       3.5184860 
3    transmembrane transporter  482   0            2       8.9616555 
4    receptor activity          388   0            2       0.8559265 
5    dehydrogenase activity     379   0            2       1.6941425 
6    receptor binding           348   0            2       2.8766101 
7    reductase activity         247   0            2       1.7956953 
8    kinase activity            240   0            2       1.9523105 
9    hydrolase activity         228   0            2       4.0766588 
10   ligase activity            187   0            2       2.9264204 
11   oxidoreductase activity    176   0            2       3.3230072 
12   methyltransferase activity 159   0            2       4.4571482 
13   channel activity           158   0            2       2.9336958 
14   acting on                  149   0            2      14.8183397 
15   activity acting            149   0            2      10.7393061 
16   oxidase activity           139   0            2       3.2990135 
17   symporter activity         134   0            2       6.4813830 
18   phosphatase activity       121   0            2       2.7666244 
19   + activity                 111   0            2       1.1940388 
20   decarboxylase activity     103   0            2       3.6508537 
21   involved in                 90   0            2      11.7311443 
22   monooxygenase activity      88   0            2       2.8384893 
23   antiporter activity         88   0            2       6.0578960 
24   adaptor activity            87   0            2       4.1003826 
25   dioxygenase activity        85   0            2       3.8256880 
26   lyase activity              82   0            2       3.4218364 
27   inhibitor activity          82   0            2       4.3775247 
28   as acceptor                 79   0            2       8.9308637 
29   activity involved           78   0            2       6.5020966 
30   RNA polymerase              78   0            2       8.3554112 
⋮    ⋮                          ⋮     ⋮            ⋮      ⋮          
2762 acyl-coa binding           2     0            2       0.57902729
2763 proton transmembrane       2     0            2       0.53125447
2764 mrna binding               2     0            2       0.50345387
2765 p receptor                 2     0            2       0.46861111
2766 sodium transporter         2     0            2       0.45112487
2767 transporter inhibitor      2     0            2       0.44608689
2768 exoribonuclease activity   2     0            2       0.53599771
2769 molecule activity          2     0            2       0.53599771
2770 receptor activator         2     0            2       0.32205292
2771 quinone binding            2     0            2       0.30589682
2772 + kinase                   2     0            2       0.26875509
2773 elongase activity          2     0            2       0.28463905
2774 receptor inhibitor         2     0            2       0.17859943
2775 cation binding             2     0            2      -0.06461576
2776 topoisomerase activity     2     0            2      -0.08317420
2777 4 binding                  2     0            2      -0.16289841
2778 group binding              2     0            2      -0.25240833
2779 + synthase                 2     0            2      -0.27729796
2780 acid reductase             2     0            2      -0.29831118
2781 trna binding               2     0            2      -0.49470831
2782 protein transmembrane      2     0            2      -0.51982340
2783 inhibitor binding          2     0            2      -0.59697139
2784 protein transporter        2     0            2      -0.75716691
2785 5 binding                  2     0            2      -0.98537491
2786 phosphatase binding        2     0            2      -1.10961327
2787 receptor k

In [ ]:
bp <- corpus_subset(corpus, ontology == "BP")
bp_tokens <- bp %>% tokens(remove_punct = TRUE)
bp_tokens %>% textstat_collocations() %>% as_tibble() %>% arrange(desc(count))

collocation             count count_nested length lambda     z         
1     regulation of           9736  0            2       9.6516094 50.227898 
2     positive regulation     3082  0            2       8.0561942 45.446861 
3     negative regulation     3046  0            2       8.4939214 38.202519 
4     biosynthetic process    2012  0            2      11.6569969  8.241132 
5     metabolic process       1729  0            2       9.8211314 15.512242 
6     response to             1647  0            2       8.2377968 54.182891 
7     catabolic process       1479  0            2      11.2126894  7.926736 
8     involved in             1376  0            2      13.1005530  9.257985 
9     signaling pathway       1031  0            2       8.8804867 67.245386 
10    cell differentiation     617  0            2       4.4113716 60.010643 
11    cellular response        600  0            2       6.2414535 66.892681 
12    of protein               382  0            2       2.1919998 29.597784 
13    cell proliferation       351  0            2       4.8281138 42.119932 
14    localization to          344  0            2       6.4048183 31.599979 
15    receptor signaling       332  0            2       4.7277275 55.944999 
16    protein localization     318  0            2       5.5049677 54.443469 
17    t cell                   304  0            2       7.1594176 20.558397 
18    transmembrane transport  282  0            2       6.1610641 45.130307 
19    plasma membrane          263  0            2       8.4383741 34.216157 
20    cell fate                255  0            2       5.1272716 33.593189 
21    of host                  247  0            2       2.3234661 24.391165 
22    apoptotic process        245  0            2       3.7492601 32.588169 
23    of cell                  237  0            2      -0.4577494 -6.723657 
24    muscle cell              212  0            2       3.0019485 34.056398 
25    cell migration           207  0            2       3.6787671 35.480457 
26    growth factor            192  0            2       7.3673004 49.087928 
27    immune response          173  0            2       5.7900417 35.601453 
28    complex assembly         171  0            2       5.8121743 44.761682 
29    pathway involved         170  0            2       5.1337889 38.530414 
30    smooth muscle            168  0            2       9.2367307 19.231957 
⋮     ⋮                       ⋮     ⋮            ⋮      ⋮          ⋮         
10298 II cell                 2     0            2      -0.3922642 -0.6136524
10299 membrane transport      2     0            2      -0.4188416 -0.6591812
10300 the cell                2     0            2      -0.5170890 -0.8098911
10301 in plasma               2     0            2      -0.5948730 -0.9352491
10302 import in               2     0            2      -0.5984173 -0.9408402
10303 by protein              2     0            2      -0.6086641 -0.9589814
10304 of location             2     0            2      -0.6305819 -0.9660557
10305 host response           2     0            2      -0.6301678 -0.9922350
10306 extension of            2     0            2      -0.6812460 -1.0452480
10307 of movement             2     0            2      -0.7294685 -1.1207705
10308 vesicle to              2     0            2      -0.7566564 -1.1889315
10309 cellular morphogenesis  2     0            2      -0.7865028 -1.2395482
10310 vascular process        2     0            2      -0.8167987 -1.2760051
10311 across cell             2     0            2      -0.8134196 -1.2769616
10312 to RNA                  2     0            2      -0.8240863 -1.2953667
10313 of precursor            2     0            2      -0.9408795 -1.4532949
10314 of follicle             2     0            2      -0.9597582 -1.4830852
10315 repair of               2     0            2      -0.9597582 -1.4830852
10316 of sulfate              2     0            2      -0.9964800 -1.5410700
10317 acid signaling        

In [ ]:
pathways <- info_tb %>% filter(grepl("pathway", term))
pathways_token <- bp %>% tokens(remove_punct = TRUE)
pathways_token %>% textstat_collocations() %>% as_tibble() %>% arrange(desc(count))
# kwic(pathways_token, "pathway")

collocation             count count_nested length lambda     z         
1     regulation of           9736  0            2       9.6516094 50.227898 
2     positive regulation     3082  0            2       8.0561942 45.446861 
3     negative regulation     3046  0            2       8.4939214 38.202519 
4     biosynthetic process    2012  0            2      11.6569969  8.241132 
5     metabolic process       1729  0            2       9.8211314 15.512242 
6     response to             1647  0            2       8.2377968 54.182891 
7     catabolic process       1479  0            2      11.2126894  7.926736 
8     involved in             1376  0            2      13.1005530  9.257985 
9     signaling pathway       1031  0            2       8.8804867 67.245386 
10    cell differentiation     617  0            2       4.4113716 60.010643 
11    cellular response        600  0            2       6.2414535 66.892681 
12    of protein               382  0            2       2.1919998 29.597784 
13    cell proliferation       351  0            2       4.8281138 42.119932 
14    localization to          344  0            2       6.4048183 31.599979 
15    receptor signaling       332  0            2       4.7277275 55.944999 
16    protein localization     318  0            2       5.5049677 54.443469 
17    t cell                   304  0            2       7.1594176 20.558397 
18    transmembrane transport  282  0            2       6.1610641 45.130307 
19    plasma membrane          263  0            2       8.4383741 34.216157 
20    cell fate                255  0            2       5.1272716 33.593189 
21    of host                  247  0            2       2.3234661 24.391165 
22    apoptotic process        245  0            2       3.7492601 32.588169 
23    of cell                  237  0            2      -0.4577494 -6.723657 
24    muscle cell              212  0            2       3.0019485 34.056398 
25    cell migration           207  0            2       3.6787671 35.480457 
26    growth factor            192  0            2       7.3673004 49.087928 
27    immune response          173  0            2       5.7900417 35.601453 
28    complex assembly         171  0            2       5.8121743 44.761682 
29    pathway involved         170  0            2       5.1337889 38.530414 
30    smooth muscle            168  0            2       9.2367307 19.231957 
⋮     ⋮                       ⋮     ⋮            ⋮      ⋮          ⋮         
10298 II cell                 2     0            2      -0.3922642 -0.6136524
10299 membrane transport      2     0            2      -0.4188416 -0.6591812
10300 the cell                2     0            2      -0.5170890 -0.8098911
10301 in plasma               2     0            2      -0.5948730 -0.9352491
10302 import in               2     0            2      -0.5984173 -0.9408402
10303 by protein              2     0            2      -0.6086641 -0.9589814
10304 of location             2     0            2      -0.6305819 -0.9660557
10305 host response           2     0            2      -0.6301678 -0.9922350
10306 extension of            2     0            2      -0.6812460 -1.0452480
10307 of movement             2     0            2      -0.7294685 -1.1207705
10308 vesicle to              2     0            2      -0.7566564 -1.1889315
10309 cellular morphogenesis  2     0            2      -0.7865028 -1.2395482
10310 vascular process        2     0            2      -0.8167987 -1.2760051
10311 across cell             2     0            2      -0.8134196 -1.2769616
10312 to RNA                  2     0            2      -0.8240863 -1.2953667
10313 of precursor            2     0            2      -0.9408795 -1.4532949
10314 of follicle             2     0            2      -0.9597582 -1.4830852
10315 repair of               2     0            2      -0.9597582 -1.4830852
10316 of sulfate              2     0            2      -0.9964800 -1.5410700
10317 acid signaling        